In [5]:
_, super_df = get_dataframes_from_folder('Newrecord/REMINE') # for mergin all dataframe in the folder....

Total Rought statistic Newrecord/REMINE : is  6162
Real Mined Statistic in Newrecord/REMINE is : 6140


In [5]:
#     =====================================================================================   #
#                                       FIRST SECTION CODE                                    # 
#     =====================================================================================   #

# IMPORTING IMPORTANT MODULE..... 
from selenium import webdriver
import requests
from bs4 import BeautifulSoup
import pandas as pd

# IMPORTING ORIGINAL DATA 
jamb_data = pd.read_csv('Newrecord/kpfile.csv')

# GETTING ATTRIBUTE FROM ORIGINAL DATA
candidate_name = jamb_data["RG_CANDNAME"].values
candidate_reg = jamb_data["RG_NUM"].values
names = list(candidate_name)
regs = list(candidate_reg)
# print(names)
# print(regs)

# GENERATING NEW DATAFRAME
gen_df = pd.DataFrame()
    
try:
    gen_df = pd.read_csv('Newrecord/REMINE/kpfile_regen1.csv', index=False)
except Exception: 
    pass

def create_dataframe(dataframe,  add=''):
    attributes = []

    for attr in dataframe.columns: 
        attributes.append(attr)
    if add != '':
        attributes.append(add)

    df = pd.DataFrame([] , columns=attributes)

    return df , attributes


if gen_df.empty:
    print('original data is empty')
    gen_df , _ = create_dataframe(jamb_data, 'Contact')

else: 
    pass
    

original data is empty


In [6]:
#     =====================================================================================   #
#                                HELPER METHOD FOR SECTION TWO                                #
#     =====================================================================================   #

from csv import writer


# helper method to valide content compatibility 

def check_content_matching(o_reg='data_reg' , o_name='d_name' , m_reg='mine_reg' , m_name = 'm_name'): 
    
    #   : o_reg / the import jamb student registration number 
    #   : o_name / the import jamb student name 
    #   : m_reg / the mined student registration number 
    #   : m_name / the mined student name 

    validate = False 
    if (m_reg.upper().strip() == o_reg.upper().strip() and m_name.lower() in o_name.lower().split()):
        validate = True
    else : 
        validate = False
        
    print('Validate : ', validate)
    return validate ; 

# helper method to had new row to the new table
def add_row(old_table , new_table, tel='',  m_reg = ''):
    
    if m_reg != '':
        d = old_table[old_table[old_table.columns[0]] == m_reg]
        old_val = d.values
#         print(old_val.flatten())
        temp_value = []
        for value in list(old_val.flatten()):
            temp_value.append(value)

#         print('TEL:' , tel)

        if tel != '':
            temp_value.append(str(tel))
            
            print(temp_value)
            new_table.loc[len(new_table)] = temp_value
            
            new_table.to_csv('Newrecord/REMINE/kpfile_regen1.csv')

#             with open('pool_abuja/generate_record9.csv') as file:
#                 wr = writer(file)
#                 wr.writerow(temp_value)
            print('Row addes successfully.....')
            return new_table
                
# add_row(jamb_data, gen_df , tel, reg_number)

In [7]:
#     =====================================================================================   #
#                                       SECOND SECTION CODE                                   #
#     =====================================================================================   #


# NAVIGATING THE WEB BROWSER USING THE STUDENT REGISTRATION NUMBER


driver= webdriver.Chrome()

def fetch_info(reg_number):
    driver.get('https://efacility.jamb.gov.ng/PrintExaminationSlip') 
    reg = driver.find_element('id' , "txtRegNumber")
    reg.send_keys(reg_number)

    # submitting form
    # reg.submit()
    sb = driver.find_element('id' , "lnkSearch")

    sb.click()
    # driver.refresh()
    # print('WEB PAGE ', driver.current_url)


    # getting data from html document
    print('fetching content')
    url = f'https://efacility.jamb.gov.ng/TempFiles/Main_Examination_Slip_{reg_number}.htm'
    page = requests.get(url)
    soup = BeautifulSoup(page.text, 'html.parser')
    data = soup.find_all('label')

    return data , len(data)


# print('Reg :', len(regs))
#  scraping through web for contact 

for index in range(0, len(regs)):
    reg = regs[index]
    name = names[index]
    
#     print(f'{SOURCE-RECOED-SIZE : ', len(regs)}')
    # ===========================================================================
    _, super_df = get_dataframes_from_folder('Newrecord/REMINE') # for mergin all dataframe in the folder....
    
#    condition if record already esist 
    if reg not in super_df["RG_NUM"].values:
        print('True')
        
        print()
        print('===================================================')
        print(f'      SOURCE RECOED-SIZE : {len(regs)}          ')
        print('---------------------------------------------------')
        print(f'   START MINING   FOR :  {reg} : index : {index}  ')
        print('===================================================')

        data , lenght = fetch_info(reg)
        if lenght != 0 :

            # printing data for confirmation
            try:
                surname = data[1].get_text()
                firstname = data[2].get_text()
                othername = data[4].get_text()
                tel = data[12].get_text()
                reg_number = data[15].get_text()

                print('Surname : ' , surname)
                print('Fist Name : ', firstname)
                print('Other Name : ',  othername)
                print('Telephone : ' , tel)
                print('Registion Number : ' , reg_number)

                print(f'main name : {reg} {name}    mined reg {reg_number} {surname}')
                valid = check_content_matching(reg, name , reg_number, surname)
                print('VALID ? ', valid)
                if valid :
                    print('                     STUDENT CONFIRMED... ')
                    add_row(jamb_data, gen_df , tel, reg_number)

            except Exception:
                print('error')

        print('==================================================')
        print(f'              END MINING     No.   {index}       ')
        print('==================================================')
        
    else:   
        print('==================================================')
        print(f'             ALREADY EXIST     No.   {index}     ')
        print('==================================================')
    
            
            

        
print('==================================================')
print(f'            FINAL   END OF MINING                ')
print('==================================================')
        

Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   0     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   1     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   2     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   3     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   4     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   5     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
        

Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   31     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   32     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   33     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   34     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   35     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   36     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
  

Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   64     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   65     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   66     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   67     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   68     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   69     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
  

Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   97     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   98     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   99     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   100     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   101     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   102     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   103     
Total

Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   130     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   131     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   132     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   133     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   134     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   135     
Total Rought statistic Newrecord/REMINE : is  26611
Real Mined Statistic in Newrecord/REMINE is : 12531
             ALREADY EXIST     No.   136     
To

...

Real Mined Statistic in Newrecord/REMINE is : 15767
             ALREADY EXIST     No.   9141     
Total Rought statistic Newrecord/REMINE : is  33083
Real Mined Statistic in Newrecord/REMINE is : 15767
             ALREADY EXIST     No.   9142     
Total Rought statistic Newrecord/REMINE : is  33083
Real Mined Statistic in Newrecord/REMINE is : 15767
             ALREADY EXIST     No.   9143     
Total Rought statistic Newrecord/REMINE : is  33083
Real Mined Statistic in Newrecord/REMINE is : 15767
             ALREADY EXIST     No.   9144     
Total Rought statistic Newrecord/REMINE : is  33083
Real Mined Statistic in Newrecord/REMINE is : 15767
             ALREADY EXIST     No.   9145     
Total Rought statistic Newrecord/REMINE : is  33083
Real Mined Statistic in Newrecord/REMINE is : 15767
             ALREADY EXIST     No.   9146     
Total Rought statistic Newrecord/REMINE : is  33083
Real Mined Statistic in Newrecord/REMINE is : 15767
             ALREADY EXIST     No.   9147 

Total Rought statistic Newrecord/REMINE : is  33083
Real Mined Statistic in Newrecord/REMINE is : 15767
             ALREADY EXIST     No.   9172     
Total Rought statistic Newrecord/REMINE : is  33083
Real Mined Statistic in Newrecord/REMINE is : 15767
             ALREADY EXIST     No.   9173     
Total Rought statistic Newrecord/REMINE : is  33083
Real Mined Statistic in Newrecord/REMINE is : 15767
             ALREADY EXIST     No.   9174     
Total Rought statistic Newrecord/REMINE : is  33083
Real Mined Statistic in Newrecord/REMINE is : 15767
             ALREADY EXIST     No.   9175     
Total Rought statistic Newrecord/REMINE : is  33083
Real Mined Statistic in Newrecord/REMINE is : 15767
             ALREADY EXIST     No.   9176     
Total Rought statistic Newrecord/REMINE : is  33083
Real Mined Statistic in Newrecord/REMINE is : 15767
             ALREADY EXIST     No.   9177     
Total Rought statistic Newrecord/REMINE : is  33083
Real Mined Statistic in Newrecord/REMINE i

Total Rought statistic Newrecord/REMINE : is  33083
Real Mined Statistic in Newrecord/REMINE is : 15767
             ALREADY EXIST     No.   9205     
Total Rought statistic Newrecord/REMINE : is  33083
Real Mined Statistic in Newrecord/REMINE is : 15767
             ALREADY EXIST     No.   9206     
Total Rought statistic Newrecord/REMINE : is  33083
Real Mined Statistic in Newrecord/REMINE is : 15767
             ALREADY EXIST     No.   9207     
Total Rought statistic Newrecord/REMINE : is  33083
Real Mined Statistic in Newrecord/REMINE is : 15767
             ALREADY EXIST     No.   9208     
Total Rought statistic Newrecord/REMINE : is  33083
Real Mined Statistic in Newrecord/REMINE is : 15767
             ALREADY EXIST     No.   9209     
Total Rought statistic Newrecord/REMINE : is  33083
Real Mined Statistic in Newrecord/REMINE is : 15767
             ALREADY EXIST     No.   9210     
Total Rought statistic Newrecord/REMINE : is  33083
Real Mined Statistic in Newrecord/REMINE i

Real Mined Statistic in Newrecord/REMINE is : 15768
             ALREADY EXIST     No.   9235     
Total Rought statistic Newrecord/REMINE : is  33085
Real Mined Statistic in Newrecord/REMINE is : 15768
             ALREADY EXIST     No.   9236     
Total Rought statistic Newrecord/REMINE : is  33085
Real Mined Statistic in Newrecord/REMINE is : 15768
             ALREADY EXIST     No.   9237     
Total Rought statistic Newrecord/REMINE : is  33085
Real Mined Statistic in Newrecord/REMINE is : 15768
             ALREADY EXIST     No.   9238     
Total Rought statistic Newrecord/REMINE : is  33085
Real Mined Statistic in Newrecord/REMINE is : 15768
             ALREADY EXIST     No.   9239     
Total Rought statistic Newrecord/REMINE : is  33085
Real Mined Statistic in Newrecord/REMINE is : 15768
             ALREADY EXIST     No.   9240     
Total Rought statistic Newrecord/REMINE : is  33085
Real Mined Statistic in Newrecord/REMINE is : 15768
             ALREADY EXIST     No.   9241 

KeyboardInterrupt: 

In [4]:
# ===================================================
#    START MINING   FOR :  202211102462IF : index : 2604 remaining    
# ===================================================

# Re-Mining section

In [2]:
#     =====================================================================================   #
#                                       REMINNING CONTENT ..                                  #
#     =====================================================================================   #

#  Load the source data = sr_df 
#  load the mined data = md_df 
#  loop through all the entire content of sr_df and get all the reg number and name
#  check if reg_number is found in md_df reg_number 
#  if found ignore ... else 
#  store in a temp array  and re-initialize the regs[] and names[] list

import pandas as pd 
import os 

def get_dataframes_from_folder(folder):
    # folder = 'pool_abuja'
    dir_list = os.listdir(folder)
#     print(dir_list)

    full_path = ''
    df_list = []
    for file in dir_list: 
        full_path = f"{folder}/{file}"
        df_list.append(pd.read_csv(full_path))
        
    total_record = 0 
    for df in df_list:
        row, _ = df.shape
        total_record += row

    print(f'Total Rought statistic {folder} : is  {total_record}')
    combined_df = pd.concat(df_list)
    combined_df.drop_duplicates(subset='RG_NUM', inplace=True)
    
#     WRITE TO CSV FILE
    combined_df.to_csv('Newrecord/REMINE/master_record.csv', index=False)
#     print(combined_df.shape)
    print(f'Real Mined Statistic in {folder} is : {combined_df.shape[0]}')
    return full_path , combined_df 





In [5]:


def re_mined(dataframe, sr_datapath = '' ):

    # load original data
    sr_df = pd.read_csv(sr_datapath)
    sr_name = sr_df["RG_CANDNAME"].values
    sr_reg = sr_df["RG_NUM"].values
    full_info = sr_df[['RG_CANDNAME', 'RG_NUM']]
    print(full_info[:3])

    # converting numpy to list array 
    regs = list(sr_name)
    names = list(sr_reg)


    # load mined data 
#     md_df = pd.read_csv('pool_abuja/generate_record.csv')
    dataframe.drop_duplicates(subset='RG_NUM', inplace=True)
    md_reg = dataframe["RG_NUM"].values


    # loop throught to filter out registration number not found in the mined document.... 
    
#     sr_temp_reg  = [reg for reg in sr_reg if not reg in md_reg]
    
    sr_temp_reg = []
    sr_temp_name = []
    
    for index in range(len(sr_reg)):
        if sr_reg[index] not in md_reg:
            sr_temp_reg.append(sr_reg[index])
            sr_temp_name.append(sr_name[index])
            

    
    name = [sr_df['RG_CANDNAME'][sr_df['RG_NUM'] == sr_temp_reg[0]]]
    print()
    print('NAME ' , name)
    remaining_data =   len(sr_reg) - len(sr_temp_reg)

    detail = f'Total Source File --> {len(sr_reg)} || Already mined --> {remaining_data} ' 
    print('Remaining record to mined Size--> ', len(sr_temp_reg))
    print(detail)
    
    return sr_temp_reg, sr_temp_name
